# Ataque al corazón

[Ver notebook interactivo](https://nbviewer.org/github/cuauhtemocbe/Diplomado-Ciencia-Datos/blob/main/notebooks/12-Ataque-corazon.ipynb)

In [3]:
%load_ext autoreload
%autoreload 2

import numpy as np
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.io as pio
import seaborn as sns
from sklearn import set_config
# from sklearn.decomposition import 
from sklearn.manifold import TSNE
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import MinMaxScaler, StandardScaler

import data_analysis_octopus as dao

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [2]:
random_seed = 333  # Semilla para reproducibilidad de resultados
np.random.seed(random_seed)  # Para reproducibilidad
# Configuración de opciones de visualización para pandas
pd.set_option("display.max_columns", None)  # Muestra todas las columnas
pd.set_option("display.max_rows", 20)  # Ajusta el número de filas a mostrar

# Configuraciones extras
sns.set_style("dark")
dark_template = pio.templates["plotly_dark"].to_plotly_json()
dark_template["layout"]["paper_bgcolor"] = "rgba(30, 30, 30, 0.5)"
dark_template["layout"]["plot_bgcolor"] = "rgba(30, 30, 30, 0)"
pio.templates["plotly_dark_semi_transparent"] = go.layout.Template(dark_template)
pio.templates.default = "plotly_dark_semi_transparent"
set_config(transform_output="pandas")
set_config(display="diagram")

%matplotlib inline

# Exploración de los datos

In [3]:
filename = "../data/Índice_de_marginalidad/diccionario_datos/diccionario_datos_iter_00CSV20.csv"
diccionario = pd.read_csv(filename, header=4)
diccionario = diccionario.dropna(axis=1, how="all").drop(columns="Unnamed: 9")

print(diccionario.shape)
diccionario.head(20)

(286, 6)


Núm.                                     Indicador  \
0      1                   Clave de entidad federativa   
1      2                            Entidad federativa   
2      3  Clave de municipio o demarcación territorial   
3      4           Municipio o demarcación territorial   
4      5                            Clave de localidad   
5      6                                     Localidad   
6      7                                      Longitud   
7      8                                       Latitud   
8      9                                       Altitud   
9      1                               Población total   
10     2                            Población femenina   
11     3                           Población masculina   
12     4                       Población de 0 a 2 años   
13     5              Población femenina de 0 a 2 años   
14     6             Población masculina de 0 a 2 años   
15     7                     Población de 3 años y más   
16     8            Población femenina de 3 años y más   
17     9           Población masculina de 3 años y más   
18    10                     Población de 5 años y más   
19    11            Población femenina de 5 años y más   

                                          Descripción   Mnemónico  \
0   Código que identifica a la entidad federativa....     ENTIDAD   
1            Nombre oficial de la entidad federativa.    NOM_ENT    
2   Código que identifica al municipio o demarcaci...         MUN   
3   Nombre oficial del municipio o demarcación ter...  NOM_MUN      
4   Código que identifica a la localidad al interi...         LOC   
5   Nombre con el que se reconoce a la localidad d...    NOM_LOC    
6   Ubicación de la localidad expresada en grados,...   LONGITUD    
7   Ubicación de la localidad expresada en grados,...     LATITUD   
8   Altura a la que se encuentra una localidad, re...     ALTITUD   
9   Total de personas que residen habitualmente en...      POBTOT   
10  Total de mujeres que residen habitualmente en ...      POBFEM   
11  Total de hombres que residen habitualmente en ...      POBMAS   
12                    Personas de 0 a 2 años de edad.       P_0A2   
13                     Mujeres de 0 a 2 años de edad.     P_0A2_F   
14                     Hombres de 0 a 2 años de edad.     P_0A2_M   
15                  Personas de 3 a 130 años de edad.     P_3YMAS   
16                   Mujeres de 3 a 130 años de edad.   P_3YMAS_F   
17                   Hombres de 3 a 130 años de edad.   P_3YMAS_M   
18                  Personas de 5 a 130 años de edad.     P_5YMAS   
19                   Mujeres de 5 a 130 años de edad.   P_5YMAS_F   

           Rangos  Longitud  
0           00…32         2  
1    Alfanumérico        50  
2         000…570         3  
3    Alfanumérico        50  
4       0000…9999         4  
5    Alfanumérico        70  
6        Caracter        16  
7        Caracter        15  
8        Caracter         4  
9   0...999999999         9  
10  0...999999999         9  
11  0...999999999         9  
12    0…999999999         9  
13  0.,.999999999         9  
14  0...999999999         9  
15  0...999999999         9  
16  0...999999999         9  
17  0...999999999         9  
18  0...999999999         9  
19  0...999999999         9

In [4]:
filename = "../data/Índice_de_marginalidad/catalogos/tam_loc.csv"
catalogos = pd.read_csv(filename)
catalogos.head(15)

tam_loc                   descripcion
0         1            1 a 249 habitantes
1         2         250 a 499 habitantes 
2         3          500 a 999 habitantes
3         4      1 000 a 2 499 habitantes
4         5      2 500 a 4 999 habitantes
5         6      5 000 a 9 999 habitantes
6         7    10 000 a 14 999 habitantes
7         8   15 000 a 29 999 habitantes 
8         9    30 000 a 49 999 habitantes
9        10    50 000 a 99 999 habitantes
10       11  100 000 a 249 999 habitantes
11       12  250 000 a 499 999 habitantes
12       13  500 000 a 999 999 habitantes
13       14    1 000 000 y más habitantes

In [5]:
filename = "../data/Índice_de_marginalidad/conjunto_de_datos/conjunto_de_datos_iter_00CSV20_nivel_municipio.csv"
df = pd.read_csv(filename)

# df = df.drop(columns=["LONGITUD", "LATITUD", "ALTITUD"])
# df =  df[df["NOM_LOC"] == "Total del Municipio"]
df["ENTIDAD"] = df["ENTIDAD"].apply(lambda x: f"{x:02}")

df = df.set_index(["ENTIDAD", "NOM_MUN"])

print(df.shape)
df.head()

(2469, 281)


NOM_ENT  MUN  LOC              NOM_LOC  POBTOT  \
ENTIDAD NOM_MUN                                                                 
01      Aguascalientes  Aguascalientes    1    0  Total del Municipio  948990   
        Asientos        Aguascalientes    2    0  Total del Municipio   51536   
        Calvillo        Aguascalientes    3    0  Total del Municipio   58250   
        Cosío           Aguascalientes    4    0  Total del Municipio   17000   
        Jesús María     Aguascalientes    5    0  Total del Municipio  129929   

                        POBFEM  POBMAS  P_0A2  P_0A2_F  P_0A2_M  P_3YMAS  \
ENTIDAD NOM_MUN                                                            
01      Aguascalientes  486917  462073  44372    21893    22479   903684   
        Asientos         26275   25261   3170     1639     1531    48346   
        Calvillo         29687   28563   3159     1581     1578    55056   
        Cosío             8708    8292   1032      539      493    15968   
        Jesús María      65710   64219   6945     3380     3565   122845   

                        P_3YMAS_F  P_3YMAS_M  P_5YMAS  P_5YMAS_F  P_5YMAS_M  \
ENTIDAD NOM_MUN                                                               
01      Aguascalientes     464556     439128   871193     448552     422641   
        Asientos            24626      23720    46095      23532      22563   
        Calvillo            28088      26968    52691      26929      25762   
        Cosío                8169       7799    15254       7798       7456   
        Jesús María         62260      60585   117571      59690      57881   

                        P_12YMAS  P_12YMAS_F  P_12YMAS_M  P_15YMAS  \
ENTIDAD NOM_MUN                                                      
01      Aguascalientes    756970      392252      364718    707473   
        Asientos           38399       19682       18717     35250   
        Calvillo           44778       23068       21710     41495   
        Cosío              12820        6622        6198     11817   
        Jesús María        99250       50684       48566     91487   

                        P_15YMAS_F  P_15YMAS_M  P_18YMAS  P_18YMAS_F  \
ENTIDAD NOM_MUN                                                        
01      Aguascalientes      368028      339445    657539      343551   
        Asientos             18088       17162     32032       16536   
        Calvillo             21446       20049     38275       19860   
        Cosío                 6125        5692     10772        5593   
        Jesús María          46899       44588     83807       43156   

                        P_18YMAS_M  P_3A5  P_3A5_F  P_3A5_M  P_6A11  P_6A11_F  \
ENTIDAD NOM_MUN                                                                 
01      Aguascalientes      313988  48767    23951    24816   97947     48353   
        Asientos             15496   3342     1632     1710    6605      3312   
        Calvillo             18415   3530     1748     1782    6748      3272   
        Cosío                 5179   1062      537      525    2086      1010   
        Jesús María          40651   7998     3903     4095   15597      7673   

                        P_6A11_M  P_8A14  P_8A14_F  P_8A14_M  P_12A14  \
ENTIDAD NOM_MUN                                                         
01      Aguascalientes     49594  114551     56248     58303    49497   
        Asientos            3293    7612      3815      3797     3149   
        Calvillo            3476    7820      3825      3995     3283   
        Cosío               1076    2374      1162      1212     1003   
        Jesús María         7924   18084      8843      9241     7763   

                        P_12A14_F  P_12A14_M  P_15A17  P_15A17_F  P_15A17_M  \
ENTIDAD NOM_MUN                                                               
01      Aguascalientes      24224      25273    49934      24477      25457   
        Asientos             1594       1555     3218       155

In [6]:
total = [
    "Población total",
    "Total de viviendas"
]

# Características a estandarizar con Población Total V1
population = [
    "Población de 3 a 5 años que no asiste a la escuela",
    "Población de 6 a 11 años que no asiste a la escuela",
    "Población de 12 a 14 años que no asiste a la escuela",
    "Población de 15 a 17 años que asiste a la escuela",
    "Población de 18 a 24 años que asiste a la escuela",
    "Población de 8 a 14 años que no sabe leer y escribir",
    "Población de 15 años y más analfabeta",
    "Población de 15 años y más sin escolaridad",
    "Población de 15 años y más con primaria incompleta",
    "Población de 15 años y más con primaria completa",
    "Población de 15 años y más con secundaria incompleta",
    "Población de 15 años y más con secundaria completa",
    "Población de 18 años y más con educación posbásica",
    "Población de 12 años y más económicamente activa",
    "Población sin afiliación a servicios de salud",
    "Población en hogares censales", # Indicador de migración
]


# Características a estandarizar con Total de viviendas V1
house = [
    "Total de viviendas particulares", # Dueños de casa propia
    "Total de viviendas particulares habitadas con características",
    "Viviendas particulares habitadas", # Indicador migración
    "Ocupantes en viviendas particulares habitadas",
    "Viviendas particulares habitadas con piso de material diferente de tierra",
    "Viviendas particulares habitadas con un dormitorio",
    "Viviendas particulares habitadas con sólo un cuarto",
    "Viviendas particulares habitadas con dos cuartos",
    "Viviendas particulares habitadas con 3 cuartos y más",
    "Viviendas particulares habitadas que disponen de energía eléctrica",
    "Viviendas particulares habitadas que disponen de agua entubada y se abastecen del servicio público de agua",
    "Viviendas particulares habitadas que disponen de tinaco",
    "Viviendas particulares habitadas que disponen de cisterna o aljibe",
    "Viviendas particulares habitadas que disponen de excusado o sanitario",
    "Viviendas particulares habitadas que disponen de drenaje",
    "Viviendas particulares habitadas que disponen de energía eléctrica, agua entubada de la red pública y drenaje",
    "Viviendas particulares habitadas que no disponen de automóvil o camioneta, ni de motocicleta o motoneta",
    "Viviendas particulares habitadas sin ningún bien",
    "Viviendas particulares habitadas que disponen de Internet",
    "Viviendas particulares habitadas con piso de tierra",
    "Viviendas particulares habitadas que no disponen de energía eléctrica",
    "Viviendas particulares habitadas que no disponen de agua entubada en el ámbito de la vivienda",
    "Viviendas particulares habitadas que no disponen de drenaje",
]

# Características que no requiere preprocesamiento
features = [
    "Promedio de hijas e hijos nacidos vivos",
    "Grado promedio de escolaridad",
    "Promedio de ocupantes en viviendas particulares habitadas",
    "Promedio de ocupantes por cuarto en viviendas particulares habitadas",
]

feat_dict = (diccionario[diccionario["Indicador"].isin(total + population + house + features)]
             .set_index("Mnemónico")["Indicador"].to_dict()
)

description_dict = {v: k for k, v in feat_dict.items()}

In [7]:
# Filtrando las características seleccionadas
feats = list(feat_dict.keys())
df = df[df.columns[df.columns.isin(feats)]]
df = df.replace(["*", "N/D"], np.nan)
df = df.astype(float)

for description in population:
    mnemonic = description_dict[description]
    
    df[mnemonic] = df[mnemonic] / df["POBTOT"]

for description in house:
    mnemonic = description_dict[description]
    
    df[mnemonic] = df[mnemonic] / df["VIVTOT"]

df = df.drop(columns=["POBTOT", "VIVTOT"])

df.head()

PROM_HNV  P3A5_NOA  P6A11_NOA  P12A14NOA   P15A17A  \
ENTIDAD NOM_MUN                                                              
01      Aguascalientes      1.98  0.019641   0.003032   0.004117  0.038451   
        Asientos            2.62  0.029281   0.005491   0.006423  0.041680   
        Calvillo            2.67  0.028979   0.004326   0.007639  0.032738   
        Cosío               2.51  0.024882   0.005824   0.004529  0.045529   
        Jesús María         2.11  0.025006   0.004056   0.006511  0.040314   

                         P18A24A   P8A14AN  P15YM_AN  P15YM_SE  P15PRI_IN  \
ENTIDAD NOM_MUN                                                             
01      Aguascalientes  0.047298  0.001950  0.012242  0.015359   0.035098   
        Asientos        0.027127  0.002096  0.024100  0.023731   0.087609   
        Calvillo        0.024996  0.002815  0.031966  0.036292   0.106970   
        Cosío           0.031824  0.002235  0.021824  0.021059   0.072647   
        Jesús María     0.039106  0.002671  0.016740  0.019957   0.050274   

                        P15PRI_CO  P15SEC_IN  P15SEC_CO  P18YM_PB  GRAPROES  \
ENTIDAD NOM_MUN                                                               
01      Aguascalientes   0.080355   0.020173   0.192352  0.373508     10.84   
        Asientos         0.098126   0.022198   0.252523  0.172540      8.54   
        Calvillo         0.132086   0.026867   0.228567  0.161408      8.05   
        Cosío            0.083471   0.014647   0.254294  0.218882      9.08   
        Jesús María      0.092781   0.024321   0.186071  0.303112     10.22   

                             PEA   PSINDER    POBHOG   TVIVPAR  VIVPAR_HAB  \
ENTIDAD NOM_MUN                                                              
01      Aguascalientes  0.512835  0.182509  0.996328  0.970558    0.822710   
        Asientos        0.416020  0.147276  0.998797  0.999088    0.816127   
        Calvillo        0.445940  0.203124  0.998369  0.995490    0.741867   
        Cosío           0.412353  0.138059  0.999824  0.998968    0.811765   
        Jesús María     0.506731  0.210107  0.999469  0.976847    0.776582   

                        VIVPARH_CV  OCUPVIVPAR  PROM_OCUP  PRO_OCUP_C  \
ENTIDAD NOM_MUN                                                         
01      Aguascalientes    0.850767    3.018314       3.54        0.84   
        Asientos          0.815606    3.352700       4.10        1.07   
        Calvillo          0.744650    2.790279       3.74        0.97   
        Cosío             0.811352    3.508153       4.32        1.14   
        Jesús María       0.798339    3.125391       3.91        0.95   

                        VPH_PISODT  VPH_PISOTI  VPH_1DOR  VPH_1CUART  \
ENTIDAD NOM_MUN                                                        
01      Aguascalientes    0.844874    0.004884  0.176970    0.010167   
        Asientos          0.803100    0.011985  0.235589    0.031720   
        Calvillo          0.735822    0.008349  0.228577    0.021447   
        Cosío             0.803096    0.008256  0.207637    0.024768   
        Jesús María       0.787461    0.009892  0.179446    0.019085   

                        VPH_2CUART  VPH_3YMASC  VPH_C_ELEC  VPH_S_ELEC  \
ENTIDAD NOM_MUN                                                          
01      Aguascalientes    0.055702    0.783975    0.848459    0.001398   
        Asientos          0.101869    0.681430    0.808962    0.006188   
        Calvillo          0.081854    0.640869    0.738797    0.005374   
        Cosío             0.101135    0.685449    0.806192    0.005160   
        Jesús María       0.073045    0.705247    0.793670    0.003730   

                        VPH_AEASP  VPH_AGUAFV  VPH_TINACO  VPH_CISTER  \
ENTIDAD NOM_MUN                                                         
01      Aguascalientes   0.811320    0.003157    0.638436    0.392015   
        Asientos         0.497427    0.008077    0.680844    0.119455   
        

### Detección y remoción de variables poco pobladas
para valores con cantidad de valores nulos > 65%

In [8]:
THRESHOLD = 65
completitud_df = dao.DataViz.completitud(df)
remove_features = completitud_df[completitud_df["% valores nulos"] >= THRESHOLD]
if remove_features.empty:
    print("No hay variables con valores nulos > 65%")
else:
    remove_features

No hay variables con valores nulos > 65%


### Detección y remoción de variables unitarias
cuando el 90% de la información se agrupe dentro de una sola variable

In [9]:
dfs_list = []
for c in df.columns:
    tmp_count = dao.count_percentage(df, c)
    
    tmp_df = tmp_count[tmp_count["porcentaje"] >= 90]

    if not tmp_df.empty:
        dfs_list.append(dao.create_feature_dataframe(tmp_df, c))

if dfs_list:
    unit_vars = pd.concat(dfs_list).reset_index(drop=True)
    unit_vars
else:
    print("No hay variables unitarias")

No hay variables unitarias


### Detección y remoción de registros con pocos valores
cuando el 70% de la información tenga valores nulos

In [10]:
# Definir el porcentaje máximo permitido de NaNs (por ejemplo, 50%)
porcentaje_maximo = 0.3

# Calcular el umbral en función del porcentaje
numero_columnas = df.shape[1]
umbral = int((1 - porcentaje_maximo) * numero_columnas)

# Eliminar filas con más del porcentaje máximo de valores NaN
print("Tamaño original: ", df.shape[0])
df = df.dropna(thresh=umbral)
print("Tamaño final: ", df.shape[0])

Tamaño original:  2469
Tamaño final:  2469


## Generación del Índice

### Principal component analysis (PCA)

In [11]:
pipe = make_pipeline(
    StandardScaler(),
    PCA()
)

pipe.fit(df)

Pipeline(steps=[('standardscaler', StandardScaler()), ('pca', PCA())])

In [12]:
pca = pipe.named_steps["pca"]

ve = pd.DataFrame(
    data    = (pca.explained_variance_ratio_ * 100).round(2),
    columns = ["variance_ratio"],
)

ve.index = [f"PCA{i}" for i in range(ve.shape[0])]

ve

variance_ratio
PCA0            31.96
PCA1            18.96
PCA2             6.85
PCA3             5.12
PCA4             3.95
...               ...
PCA38            0.01
PCA39            0.00
PCA40            0.00
PCA41            0.00
PCA42            0.00

[43 rows x 1 columns]

### Diagrama de Codo

In [13]:
explained_variance = 100 - np.cumsum(pca.explained_variance_ratio_ * 100)

pricipal_components = list(range(1, len(explained_variance) + 1))

# Crea el diagrama de codo utilizando Plotly
trace = go.Scatter(x=pricipal_components, y=explained_variance, mode="lines+markers")
layout = go.Layout(title="Diagrama de Codo",
                     xaxis=dict(title="Número de Componentes Principales"),
                     yaxis=dict(title="Varianza Explicada (%)"),
                     hovermode="closest")

fig = go.Figure(data=[trace], layout=layout)
pio.show(fig)


In [14]:
pipe.named_steps["pca"].components_[0,:] *= -1

tr = pd.DataFrame(
    data    = pipe.named_steps["pca"].components_[0:2,:],
    columns = df.columns,
    index   = ["PC0", "PC1"]
).T

tr["Característica"] = tr.index
tr["Característica"] = tr["Característica"].replace(feat_dict)

tr.sort_values("PC0", ascending=False)

PC0       PC1  \
P15YM_AN    0.214296  0.104249   
PROM_HNV    0.205797 -0.074739   
P15YM_SE    0.196988  0.108130   
VPH_SNBIEN  0.184899  0.148466   
P15PRI_IN   0.177305 -0.077391   
...              ...       ...   
VPH_EXCSA  -0.221740  0.107753   
VPH_C_SERV -0.223273  0.099219   
VPH_INTER  -0.225131  0.017326   
P18YM_PB   -0.228231 -0.011895   
GRAPROES   -0.243116 -0.037111   

                                               Característica  
P15YM_AN                Población de 15 años y más analfabeta  
PROM_HNV              Promedio de hijas e hijos nacidos vivos  
P15YM_SE           Población de 15 años y más sin escolaridad  
VPH_SNBIEN   Viviendas particulares habitadas sin ningún bien  
P15PRI_IN   Población de 15 años y más con primaria incomp...  
...                                                       ...  
VPH_EXCSA   Viviendas particulares habitadas que disponen ...  
VPH_C_SERV  Viviendas particulares habitadas que disponen ...  
VPH_INTER   Viviendas particulares habitadas que disponen ...  
P18YM_PB    Población de 18 años y más con educación posbá...  
GRAPROES                        Grado promedio de escolaridad  

[43 rows x 3 columns]

In [15]:
features_to_plot = tr.sort_values("PC0", ascending=False).head(5).index.to_list()

In [16]:
components = pipe.transform(df).reset_index()
loadings = pipe["pca"].components_.T * np.sqrt(pipe["pca"].explained_variance_)
loadings_txt = pipe["pca"].components_.T

dfi = (components.rename({"pca0":"Indice de Marginación"}, axis=1)
       .iloc[:,:3].set_index(["ENTIDAD", "NOM_MUN"]))

scaler = MinMaxScaler()
dfi_scl = scaler.fit_transform(dfi).reset_index()
dfi_scl["Indice de Marginación"] = dfi_scl["Indice de Marginación"].round(2)

### Ciudades con menor marginación

In [17]:
lowest_df = dfi_scl.sort_values(["Indice de Marginación"], ascending=True).head(20)
lowest_df

ENTIDAD                   NOM_MUN  Indice de Marginación
285       09             Benito Juárez                   0.00
274       09                  Coyoacán                   0.04
287       09            Miguel Hidalgo                   0.05
976       19    San Pedro Garza García                   0.06
286       09                Cuauhtémoc                   0.07
717       15                   Metepec                   0.07
273       09              Azcapotzalco                   0.07
784       15        Cuautitlán Izcalli                   0.08
683       15   Coacalco de Berriozábal                   0.08
277       09                 Iztacalco                   0.08
288       09       Venustiano Carranza                   0.08
275       09     Cuajimalpa de Morelos                   0.08
281       09            Álvaro Obregón                   0.09
1003      19  San Nicolás de los Garza                   0.09
1358      20       San Sebastián Tutla                   0.09
1801      22               Corregidora                   0.09
676       15      Atizapán de Zaragoza                   0.09
279       09    La Magdalena Contreras                   0.10
276       09         Gustavo A. Madero                   0.10
283       09                   Tlalpan                   0.10

### Ciudades con mayor marginación

In [18]:
highest_df = dfi_scl.sort_values(["Indice de Marginación"], ascending=False).head(20)
highest_df

ENTIDAD                          NOM_MUN  Indice de Marginación
213       08  Batopilas de Manuel Gómez Morín                   1.00
451       12               Cochoapa el Grande                   0.93
103       07                    Chalchihuitán                   0.91
1458      20               Santiago Amoltepec                   0.85
1024      20           Coicoyán de las Flores                   0.84
302       10                        Mezquital                   0.83
163       07                           Sitalá                   0.82
946       18                        Del Nayar                   0.81
1179      20                 San José Tenango                   0.81
2202      30             Mixtla de Altamirano                   0.79
416       12                       Metlatónoc                   0.77
1250      20                 San Martín Peras                   0.77
1177      20           San José Independencia                   0.77
1474      20               Santiago Ixtayutla                   0.77
1220      20                 San Juan Petlapa                   0.77
2251      30                       Tehuipango                   0.77
270       08                           Urique                   0.76
599       14                        Mezquitic                   0.76
217       08                          Carichí                   0.76
137       07                         Mitontic                   0.76

In [19]:
dfi_scl["label"] = "neutro"

for _, row in lowest_df.iterrows():
    entidad = row["ENTIDAD"]
    municipio = row["NOM_MUN"]

    dfi_scl.loc[(dfi_scl["ENTIDAD"] == entidad) & (dfi_scl["NOM_MUN"] == municipio), "label"] = "Menor marginación"


for _, row in highest_df.iterrows():
    entidad = row["ENTIDAD"]
    municipio = row["NOM_MUN"]

    dfi_scl.loc[(dfi_scl["ENTIDAD"] == entidad) & (dfi_scl["NOM_MUN"] == municipio), "label"] = "Mayor marginación"

In [20]:
dfi_scl.value_counts("label")

label
neutro               2429
Mayor marginación      20
Menor marginación      20
Name: count, dtype: int64

### Distribución

In [21]:
dfi_scl.describe().round(2)

Indice de Marginación
count                2469.00
mean                    0.41
std                     0.13
min                     0.00
25%                     0.32
50%                     0.40
75%                     0.49
max                     1.00

In [22]:
merged_df = (
    components.merge(dfi_scl, on=["ENTIDAD", "NOM_MUN"])
    .rename(columns={"NOM_MUN": "Municipio"})
)

In [23]:
def create_hover_text(df):
    return (
        df["Municipio"] + "<br>" + 
        "Indice de Marginación: " + df["Indice de Marginación"].astype(str) + "<br>" +
        "pca0: " + df["pca0"].round(2).astype(str) + "<br>" +
        "pca1: " + df["pca1"].round(2).astype(str)
    )

# Aplicar la función a los dataframes
merged_df["hover_text"] = create_hover_text(merged_df)
filtered_df = merged_df[merged_df["label"].isin(["Mayor marginación", "Menor marginación"])]
filtered_df["hover_text"] = create_hover_text(filtered_df)

trace1 = go.Scatter(
    x=merged_df["pca0"],
    y=merged_df["pca1"],
    mode="markers",
    marker=dict(
        color=merged_df["Indice de Marginación"],
        colorbar=dict(title="Indice de Marginación")
    ),
    text=merged_df["hover_text"],
    hoverinfo="text",
    name="Indice de Marginación",
    legendgroup="group1"
)

trace2 = go.Scatter(
    x=filtered_df["pca0"],
    y=filtered_df["pca1"],
    mode="markers",
    marker=dict(
        color=filtered_df["label"].map({"Menor marginación": "blue", "Mayor marginación": "red"})
    ),
    text=filtered_df["hover_text"],
    hoverinfo="text",
    name="Label",
    legendgroup="group2"
)

# Crear la figura con make_subplots
fig = make_subplots(specs=[[{"secondary_y": False}]])

# Agregar trazas a la figura
fig.add_trace(trace1)
fig.add_trace(trace2)

# features = df.columns.to_list()[:5]
features = features_to_plot
for i, feature in enumerate(features):
    fig.add_annotation(
        ax=0, ay=0,
        axref="x", ayref="y",
        x=loadings[i, 0],
        y=loadings[i, 1],
        showarrow=True,
        arrowcolor="orange",
        arrowsize=2,
        arrowhead=2,
        xanchor="right",
        yanchor="top"
    )
    fig.add_annotation(
        x=loadings[i, 0],
        y=loadings[i, 1],
        font=dict(color="orange",size=10),
        ax=0, ay=0,
        xanchor="center",
        yanchor="bottom",
        text=feat_dict[feature] + " (" + str(loadings_txt[i, 0].round(2)) + " , " +
                            str(loadings_txt[i, 1].round(2)) + ")",
        yshift=5,
    )

fig.update_traces(textposition="top center", textfont_size=10)
fig.update_layout(
    title="Biplot PCA",
    xaxis_title="PC0",
    yaxis_title="PC1",
    legend_title_text="Leyenda",
    legend=dict(x=0, y=1, traceorder="normal"),
    width=1200,
    height=800
)
# fig.update_yaxes(autorange="reversed")
fig.show()

/tmp/ipykernel_21834/1141538771.py:12: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



## Índice de Marginación en CDMX 

In [24]:
shapefile_path = "../data/Alcaldias_CDMX/alcaldias_cdmx.shp"
gdf = gpd.read_file(shapefile_path)

gdf = gdf[gdf["CVE_ENT"].isin(["09"])]
gdf = gdf.merge(dfi_scl, how="left", left_on=["CVE_ENT", "NOMGEO"], right_on=["ENTIDAD", "NOM_MUN"])

gdf = gdf.rename(columns={"NOM_MUN": "Alcaldía"}).set_index("Alcaldía")
gdf = gdf.to_crs(epsg=4326)
gdf

CVEGEO CVE_ENT CVE_MUN                  NOMGEO  \
Alcaldía                                                                
Azcapotzalco            09002      09     002            Azcapotzalco   
Coyoacán                09003      09     003                Coyoacán   
Cuajimalpa de Morelos   09004      09     004   Cuajimalpa de Morelos   
Gustavo A. Madero       09005      09     005       Gustavo A. Madero   
Iztacalco               09006      09     006               Iztacalco   
Iztapalapa              09007      09     007              Iztapalapa   
La Magdalena Contreras  09008      09     008  La Magdalena Contreras   
Milpa Alta              09009      09     009              Milpa Alta   
Álvaro Obregón          09010      09     010          Álvaro Obregón   
Tláhuac                 09011      09     011                 Tláhuac   
Tlalpan                 09012      09     012                 Tlalpan   
Xochimilco              09013      09     013              Xochimilco   
Benito Juárez           09014      09     014           Benito Juárez   
Cuauhtémoc              09015      09     015              Cuauhtémoc   
Miguel Hidalgo          09016      09     016          Miguel Hidalgo   
Venustiano Carranza     09017      09     017     Venustiano Carranza   

                                                                 geometry  \
Alcaldía                                                                    
Azcapotzalco            POLYGON ((-99.18231 19.50748, -99.18229 19.507...   
Coyoacán                POLYGON ((-99.13427 19.35654, -99.13397 19.356...   
Cuajimalpa de Morelos   POLYGON ((-99.25738 19.40112, -99.25698 19.400...   
Gustavo A. Madero       POLYGON ((-99.11124 19.5615, -99.11485 19.5576...   
Iztacalco               POLYGON ((-99.05751 19.40673, -99.05753 19.406...   
Iztapalapa              POLYGON ((-99.01692 19.38187, -99.01652 19.381...   
La Magdalena Contreras  POLYGON ((-99.20819 19.33674, -99.20859 19.336...   
Milpa Alta              POLYGON ((-98.99718 19.22747, -98.99723 19.227...   
Álvaro Obregón          POLYGON ((-99.18906 19.39559, -99.18871 19.394...   
Tláhuac                 POLYGON ((-98.97881 19.32392, -98.97856 19.323...   
Tlalpan                 POLYGON ((-99.19671 19.3024, -99.19629 19.3022...   
Xochimilco              POLYGON ((-99.0988 19.32045, -99.0987 19.31964...   
Benito Juárez           POLYGON ((-99.14762 19.40401, -99.14681 19.403...   
Cuauhtémoc              POLYGON ((-99.12951 19.46265, -99.12919 19.462...   
Miguel Hidalgo          POLYGON ((-99.19045 19.47044, -99.19058 19.467...   
Venustiano Carranza     POLYGON ((-99.10946 19.45292, -99.10895 19.452...   

                       ENTIDAD  Indice de Marginación              label  
Alcaldía                                                                  
Azcapotzalco                09                   0.07  Menor marginación  
Coyoacán                    09                   0.04  Menor marginación  
Cuajimalpa de Morelos       09                   0.08  Menor marginación  
Gustavo A. Madero           09                   0.10  Menor marginación  
Iztacalco                   09                   0.08  Menor marginación  
Iztapalapa                  09                   0.11             neutro  
La Magdalena Contreras      09                   0.10  Menor marginación  
Milpa Alta                  09                   0.19             neutro  
Álvaro Obregón              09                   0.09  Menor marginación  
Tláhuac                     09                   0.13             neutro  
Tlalpan                     09                   0.10  Menor marginación  
Xochimilco                  09                   0.14             neutro  
Benito Juárez               09                   0.00  Menor marginación  
Cuauhtémoc                  09                   0.07  Menor marginación  
Miguel Hidalgo              09                   0.05  Menor marginación  
Venustiano Carranza         09                

In [25]:
fig = px.choropleth(gdf, geojson=gdf.geometry, 
                    locations=gdf.index, color="Indice de Marginación",
                    height=500,
                   color_continuous_scale=["#F2D7D5", "#922B21"]
)

fig.update_geos(fitbounds="locations", visible=True)

fig.update_layout(
    title_text="Mapa de Índice de Marginación en la CDMX"
)

fig.update(layout = dict(title=dict(x=0.5)))

fig.update_traces(
    marker_line_color="white",
    marker_line_width=0.5
)

fig.update_layout(
    margin={"r":50,"t":50,"l":50,"b":50},
    coloraxis_colorbar={
        "title": "Indice de Marginación"
    }
)
    
fig.show()